In [1]:
import dask.dataframe as dd
from dask.distributed import Client, wait
import pandas as pd
import numpy as np
from dask_ml.preprocessing import DummyEncoder
from dask_ml.impute import SimpleImputer as si
from dask_ml.preprocessing import StandardScaler as ss
from dask_ml.decomposition import IncrementalPCA
import dask.array as da
import pickle

In [2]:
client = Client()
input_filename = '../Data/gee_features.csv'
label_filename = '../Data/training_label.csv'
with open('../Data/null_cols.pkl', 'rb') as f:
    null_cols = pickle.load(f)
with open('../Data/low_variance_cols.pkl', 'rb') as f:
    low_variance_cols = pickle.load(f)
pred_cols = ["Mean_BMI","Median_BMI","Unmet_Need_Rate","Under5_Mortality_Rate","Skilled_Birth_Attendant_Rate","Stunted_Rate"]

/opt/miniconda3/envs/ml2/lib/python3.10/site-packages/distributed/dashboard/core.py:20: UserWarning: 
Dask needs bokeh >= 2.4.2, < 3 for the dashboard.
You have bokeh==3.1.1.
Continuing without the dashboard.
  warnings.warn(
2023-06-15 16:13:56,911 - distributed.diskutils - INFO - Found stale lock file and directory '/var/folders/qb/stptmtq13_9gt1v1pzd4g4s00000gn/T/dask-worker-space/worker-t0j8u_ha', purging
2023-06-15 16:13:56,912 - distributed.diskutils - INFO - Found stale lock file and directory '/var/folders/qb/stptmtq13_9gt1v1pzd4g4s00000gn/T/dask-worker-space/worker-3cfusytw', purging
2023-06-15 16:13:56,912 - distributed.diskutils - INFO - Found stale lock file and directory '/var/folders/qb/stptmtq13_9gt1v1pzd4g4s00000gn/T/dask-worker-space/worker-ta58swkz', purging
2023-06-15 16:13:56,913 - distributed.diskutils - INFO - Found stale lock file and directory '/var/folders/qb/stptmtq13_9gt1v1pzd4g4s00000gn/T/dask-worker-space/worker-4e68jmn3', purging


In [3]:
df = dd.read_csv(input_filename, sample=1000000, usecols = lambda x: x not in 
                     ['new_ind', 'index', 'ADM1DHS', 'ADM1FIPS', 'ADM1FIPSNA', 'ADM1NAME', 
                      'ADM1SALBCO', 'ADM1SALBNA', 'ADM1SALNA', 'ALT_DEM', 'ALT_GPS', 'CCFIPS',
                     'DATUM', 'F21', 'F22', 'F23', 'ZONECO', 'ZONENA', 'DHSCLUST', 'DHSREGCO', 'SOURCE',
                     'key1', 'key2', 'key3'], dtype={'DHSID': 'str'}).set_index('DHSID')
df.head()

DHSCC DHSREGNA  DHSYEAR     LATNUM    LONGNUM URBAN_RURA  \
DHSID                                                                     
AL200800000001    AL  central     2008  40.822650  19.838322          R   
AL200800000002    AL  central     2008  40.696846  20.007555          R   
AL200800000003    AL  central     2008  40.750040  19.974262          R   
AL200800000004    AL  central     2008  40.798930  19.863338          R   
AL200800000005    AL  central     2008  40.746124  19.843885          R   

                elevation@AHN/AHN2_05M_INT  elevation_max@AHN/AHN2_05M_INT  \
DHSID                                                                        
AL200800000001                         NaN                             NaN   
AL200800000002                         NaN                             NaN   
AL200800000003                         NaN                             NaN   
AL200800000004                         NaN                             NaN   
AL200800000005                         NaN                             NaN   

                elevation_min@AHN/AHN2_05M_INT  elevation@AHN/AHN2_05M_NON  \
DHSID                                                                        
AL200800000001                             NaN                         NaN   
AL200800000002                             NaN                         NaN   
AL200800000003                             NaN                         NaN   
AL200800000004                             NaN                         NaN   
AL200800000005                             NaN                         NaN   

                ...  motorized_only_friction_surface_20000  \
DHSID           ...                                          
AL200800000001  ...                               0.011207   
AL200800000002  ...                               0.010277   
AL200800000003  ...                               0.010316   
AL200800000004  ...                               0.010585   
AL200800000005  ...                               0.009745   

                motorized_only_travel_time_20000  \
DHSID                                              
AL200800000001                         16.502903   
AL200800000002                         34.382580   
AL200800000003                         27.699300   
AL200800000004                         16.992321   
AL200800000005                         20.305431   

                walking_only_friction_surface_50000  \
DHSID                                                 
AL200800000001                             0.031108   
AL200800000002                             0.035934   
AL200800000003                             0.032862   
AL200800000004                             0.031864   
AL200800000005                             0.034980   

                walking_only_travel_time_50000  \
DHSID                                            
AL200800000001                       226.56590   
AL200800000002                       225.83365   
AL200800000003                       225.12117   
AL200800000004                       233.25563   
AL200800000005                       249.49501   

                motorized_only_friction_surface_50000  \
DHSID                                                   
AL200800000001                               0.025174   
AL200800000002                               0.029437   
AL200800000003                               0.026694   
AL200800000004                               0.025747   
AL200800000005                               0.027163   

                motorized_only_travel_time_50000  \
DHSID                                              
AL200800000001                         52.417587   
AL200800000002                         56.164467   
AL200800000003                         52.411550   
AL200800000004                         53.518450   
AL200800000005                         58.282570   

                walking_only_friction_surface_100000  \
DHSID                                

In [5]:
imp_cols = df.columns[:6]
df1 = df[imp_cols]
df1

Dask DataFrame Structure:
                  DHSCC DHSREGNA DHSYEAR   LATNUM  LONGNUM URBAN_RURA
npartitions=136                                                      
AL200800000001   object   object   int64  float64  float64     object
AL201700000422      ...      ...     ...      ...      ...        ...
...                 ...      ...     ...      ...      ...        ...
ZW200500000896      ...      ...     ...      ...      ...        ...
ZW201500000400      ...      ...     ...      ...      ...        ...
Dask Name: getitem, 8 graph layers

In [6]:
df1.to_parquet('../Data/other_data/')

2023-06-15 15:44:30,753 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:31,596 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:31,937 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:32,432 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:32,913 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:33,358 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:37,110 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 15:44:37,528 - distributed.utils_perf - WARNING - full garbage collections took

In [8]:
df = df.drop(imp_cols, axis=1)
df.head()

elevation@AHN/AHN2_05M_INT  elevation_max@AHN/AHN2_05M_INT  \
DHSID                                                                        
AL200800000001                         NaN                             NaN   
AL200800000002                         NaN                             NaN   
AL200800000003                         NaN                             NaN   
AL200800000004                         NaN                             NaN   
AL200800000005                         NaN                             NaN   

                elevation_min@AHN/AHN2_05M_INT  elevation@AHN/AHN2_05M_NON  \
DHSID                                                                        
AL200800000001                             NaN                         NaN   
AL200800000002                             NaN                         NaN   
AL200800000003                             NaN                         NaN   
AL200800000004                             NaN                         NaN   
AL200800000005                             NaN                         NaN   

                elevation_max@AHN/AHN2_05M_NON  \
DHSID                                            
AL200800000001                             NaN   
AL200800000002                             NaN   
AL200800000003                             NaN   
AL200800000004                             NaN   
AL200800000005                             NaN   

                elevation_min@AHN/AHN2_05M_NON  elevation@AHN/AHN2_05M_RUW  \
DHSID                                                                        
AL200800000001                             NaN                         NaN   
AL200800000002                             NaN                         NaN   
AL200800000003                             NaN                         NaN   
AL200800000004                             NaN                         NaN   
AL200800000005                             NaN                         NaN   

                elevation_max@AHN/AHN2_05M_RUW  \
DHSID                                            
AL200800000001                             NaN   
AL200800000002                             NaN   
AL200800000003                             NaN   
AL200800000004                             NaN   
AL200800000005                             NaN   

                elevation_min@AHN/AHN2_05M_RUW  \
DHSID                                            
AL200800000001                             NaN   
AL200800000002                             NaN   
AL200800000003                             NaN   
AL200800000004                             NaN   
AL200800000005                             NaN   

                ET_water_median@CAS/IGSNRR/PML/V2&timestamped  ...  \
DHSID                                                          ...   
AL200800000001                                      -0.802911  ...   
AL200800000002                                      -0.802911  ...   
AL200800000003                                      -0.802911  ...   
AL200800000004                                      -0.802911  ...   
AL200800000005                                      -0.802911  ...   

                motorized_only_friction_surface_20000  \
DHSID                                                   
AL200800000001                               0.011207   
AL200800000002                               0.010277   
AL200800000003                               0.010316   
AL200800000004                               0.010585   
AL200800000005                               0.009745   

                motorized_only_travel_time_20000  \
DHSID                                              
AL200800000001                         16.502903   
AL200800000002                         34.382580   
AL200800000003                         27.699300   
AL200800000004                         16.992321   
AL200800000005                         20.305431   

                walking_only_friction_surface_50000  \
DHSID      

In [9]:
df.to_parquet('../Data/main_data/')

2023-06-15 16:05:24,721 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:27,349 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-06-15 16:05:27,832 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:28,982 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:30,375 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:38,846 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:38,875 - distributed.utils_perf - WARNING - full garbage collections took 11% CPU time recently (threshold: 10%)
2023-06-15 16:05:40,378 - distributed.utils_perf - WARNING - full garbage collections took

In [3]:
df = dd.read_parquet('../Data/main_data/')
nulls = df.isnull().sum().compute()
nulls

2023-06-15 16:14:44,960 - distributed.utils_perf - WARNING - full garbage collections took 22% CPU time recently (threshold: 10%)
2023-06-15 16:14:45,743 - distributed.utils_perf - WARNING - full garbage collections took 22% CPU time recently (threshold: 10%)
2023-06-15 16:14:46,128 - distributed.utils_perf - WARNING - full garbage collections took 22% CPU time recently (threshold: 10%)
2023-06-15 16:14:46,920 - distributed.utils_perf - WARNING - full garbage collections took 22% CPU time recently (threshold: 10%)
2023-06-15 16:14:47,480 - distributed.utils_perf - WARNING - full garbage collections took 22% CPU time recently (threshold: 10%)
2023-06-15 16:14:47,876 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
2023-06-15 16:14:48,351 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
2023-06-15 16:14:48,777 - distributed.utils_perf - WARNING - full garbage collections took

elevation@AHN/AHN2_05M_INT                120984
elevation_max@AHN/AHN2_05M_INT            120984
elevation_min@AHN/AHN2_05M_INT            120984
elevation@AHN/AHN2_05M_NON                120984
elevation_max@AHN/AHN2_05M_NON            120984
                                           ...  
motorized_only_travel_time_50000               0
walking_only_friction_surface_100000           0
walking_only_travel_time_100000                0
motorized_only_friction_surface_100000         0
motorized_only_travel_time_100000              0
Length: 11914, dtype: int64

In [11]:
nulls[nulls > 0].shape

(596,)

In [10]:
nulls.to_csv('../Data/nulls.csv')

In [19]:
nulls[nulls>0].index

Index(['elevation@AHN/AHN2_05M_INT', 'elevation_max@AHN/AHN2_05M_INT',
       'elevation_min@AHN/AHN2_05M_INT', 'elevation@AHN/AHN2_05M_NON',
       'elevation_max@AHN/AHN2_05M_NON', 'elevation_min@AHN/AHN2_05M_NON',
       'elevation@AHN/AHN2_05M_RUW', 'elevation_max@AHN/AHN2_05M_RUW',
       'elevation_min@AHN/AHN2_05M_RUW',
       'data_composition@CPOM/CryoSat2/ANTARCTICA_DEM',
       ...
       'QC_kurtosis@UMT/NTSG/v2/MODIS/NPP&timestamped',
       'annualNPP_kurtosis@UMT/NTSG/v2/MODIS/NPP&timestamped',
       'QC_skew@UMT/NTSG/v2/MODIS/NPP&timestamped',
       'annualNPP_skew@UMT/NTSG/v2/MODIS/NPP&timestamped',
       'population_kurtosis@WorldPop/GP/100m/pop&timestamped',
       'population_skew@WorldPop/GP/100m/pop&timestamped',
       'water_kurtosis@GLCF/GLS_WATER&timestamped',
       'water_skew@GLCF/GLS_WATER&timestamped',
       'change-confidence_kurtosis@COPERNICUS/Landcover/100m/Proba-V-C3/Global&timestamped',
       'change-confidence_skew@COPERNICUS/Landcover/100m/Pr

In [20]:
df = dd.read_parquet('../Data/main_data/')
df = df.drop(nulls[nulls>0].index, axis=1)
df

Dask DataFrame Structure:
                ET_water_median@CAS/IGSNRR/PML/V2&timestamped Ec_median@CAS/IGSNRR/PML/V2&timestamped Ei_median@CAS/IGSNRR/PML/V2&timestamped Es_median@CAS/IGSNRR/PML/V2&timestamped GPP_median@CAS/IGSNRR/PML/V2&timestamped qc_median@CAS/IGSNRR/PML/V2&timestamped ET_water_mean@CAS/IGSNRR/PML/V2&timestamped Ec_mean@CAS/IGSNRR/PML/V2&timestamped Ei_mean@CAS/IGSNRR/PML/V2&timestamped Es_mean@CAS/IGSNRR/PML/V2&timestamped GPP_mean@CAS/IGSNRR/PML/V2&timestamped qc_mean@CAS/IGSNRR/PML/V2&timestamped ET_water_max_max@CAS/IGSNRR/PML/V2&timestamped ET_water_max_min@CAS/IGSNRR/PML/V2&timestamped ET_water_min_max@CAS/IGSNRR/PML/V2&timestamped ET_water_min_min@CAS/IGSNRR/PML/V2&timestamped Ec_max_max@CAS/IGSNRR/PML/V2&timestamped Ec_max_min@CAS/IGSNRR/PML/V2&timestamped Ec_min_max@CAS/IGSNRR/PML/V2&timestamped Ec_min_min@CAS/IGSNRR/PML/V2&timestamped Ei_max_max@CAS/IGSNRR/PML/V2&timestamped Ei_max_min@CAS/IGSNRR/PML/V2&timestamped Ei_min_max@CAS/IGSNRR/PML/V2&timestamped Ei_min_min@CAS/IGSNRR/PML/V2&timestamped Es_max_max@CAS/IGSNRR/PML/V2&timestamped Es_max_min@CAS/IGSNRR/PML/V2&timestamped Es_min_max@CAS/IGSNRR/PML/V2&timestamped Es_min_min@CAS/IGSNRR/PML/V2&timestamped GPP_max_max@CAS/IGSNRR/PML/V2&timestamped GPP_max_min@CAS/IGSNRR/PML/V2&timestamped GPP_min_max@CAS/IGSNRR/PML/V2&timestamped GPP_min_min@CAS/IGSNRR/PML/V2&timestamped qc_max_max@CAS/IGSNRR/PML/V2&timestamped qc_max_min@CAS/IGSNRR/PML/V2&timestamped qc_min_max@CAS/IGSNRR/PML/V2&timestamped qc_min_min@CAS/IGSNRR/PML/V2&timestamped elevation@CGIAR/SRTM90_V4 elevation_max@CGIAR/SRTM90_V4 elevation_min@CGIAR/SRTM90_V4 basic_demographic_characteristics_median@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped basic_demographic_characteristics_mean@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped basic_demographic_characteristics_max_max@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped basic_demographic_characteristics_max_min@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped basic_demographic_characteristics_min_max@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped basic_demographic_characteristics_min_min@CIESIN/GPWv411/GPW_Basic_Demographic_Characteristics&timestamped data_context@CIESIN/GPWv411/GPW_Data_Context data_context_max@CIESIN/GPWv411/GPW_Data_Context data_context_min@CIESIN/GPWv411/GPW_Data_Context land_area@CIESIN/GPWv411/GPW_Land_Area land_area_max@CIESIN/GPWv411/GPW_Land_Area land_area_min@CIESIN/GPWv411/GPW_Land_Area mean_administrative_unit_area@CIESIN/GPWv411/GPW_Mean_Administrative_Unit_Area mean_administrative_unit_area_max@CIESIN/GPWv411/GPW_Mean_Administrative_Unit_Area mean_administrative_unit_area_min@CIESIN/GPWv411/GPW_Mean_Administrative_Unit_Area national_identifier_grid@CIESIN/GPWv411/GPW_National_Identifier_Grid national_identifier_grid_max@CIESIN/GPWv411/GPW_National_Identifier_Grid national_identifier_grid_min@CIESIN/GPWv411/GPW_National_Identifier_Grid population_count_median@CIESIN/GPWv411/GPW_Population_Count&timestamped population_count_mean@CIESIN/GPWv411/GPW_Population_Count&timestamped population_count_max_max@CIESIN/GPWv411/GPW_Population_Count&timestamped population_count_max_min@CIESIN/GPWv411/GPW_Population_Count&timestamped population_count_min_max@CIESIN/GPWv411/GPW_Population_Count&timestamped population_count_min_min@CIESIN/GPWv411/GPW_Population_Count&timestamped population_density_median@CIESIN/GPWv411/GPW_Population_Density&timestamped population_density_mean@CIESIN/GPWv411/GPW_Population_Density&timestamped population_density_max_max@CIESIN/GPWv411/GPW_Population_Density&timestamped population_density_max_min@CIESIN/GPWv411/GPW_Population_Density&timestamped population_density_min_max@CIESIN/GPWv411/GPW_Population_Density&timestamped population_density_min_min@CIESIN/GPWv411/GPW_Population_Density&timestamped unwpp-adjusted_population_count_median@CIESIN/GPWv411/GPW_UNWPP-Adjusted_Population_Count&timestamped unwpp-adjusted_pop

In [21]:
df.head()

2023-06-15 16:29:30,893 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:31,954 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,040 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,269 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,402 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,611 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,698 - distributed.utils_perf - WARNING - full garbage collections took 12% CPU time recently (threshold: 10%)
2023-06-15 16:29:32,817 - distributed.utils_perf - WARNING - full garbage collections took

ET_water_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                           
AL200800000001                                      -0.802911   
AL200800000002                                      -0.802911   
AL200800000003                                      -0.802911   
AL200800000004                                      -0.802911   
AL200800000005                                      -0.802911   

                Ec_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                     
AL200800000001                                 0.697994   
AL200800000002                                 0.546368   
AL200800000003                                 0.474569   
AL200800000004                                 0.793127   
AL200800000005                                 0.689465   

                Ei_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                     
AL200800000001                                 0.051240   
AL200800000002                                 0.072052   
AL200800000003                                 0.040593   
AL200800000004                                 0.056218   
AL200800000005                                 0.072462   

                Es_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                     
AL200800000001                                 0.720611   
AL200800000002                                 0.641110   
AL200800000003                                 0.809169   
AL200800000004                                 0.680800   
AL200800000005                                 0.696633   

                GPP_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                      
AL200800000001                                  2.867798   
AL200800000002                                  2.831818   
AL200800000003                                  2.093236   
AL200800000004                                  3.167071   
AL200800000005                                  2.979739   

                qc_median@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                     
AL200800000001                                      0.0   
AL200800000002                                      0.0   
AL200800000003                                      0.0   
AL200800000004                                      0.0   
AL200800000005                                      0.0   

                ET_water_mean@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                         
AL200800000001                                    -0.385094   
AL200800000002                                    -0.385094   
AL200800000003                                    -0.385094   
AL200800000004                                    -0.385094   
AL200800000005                                    -0.385094   

                Ec_mean@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                   
AL200800000001                               1.004067   
AL200800000002                               0.949528   
AL200800000003                               0.784751   
AL200800000004                               1.091989   
AL200800000005                               0.930896   

                Ei_mean@CAS/IGSNRR/PML/V2&timestamped  \
DHSID                                                   
AL200800000001                               0.063028   
AL200800000002                               0.080869   
AL200800000003                               0.055926   
AL200800000004                               0.066411   
AL200800000005                               0.080958   

                Es_mean@CAS/IGSNRR/PML/V2&timestamped  ...  \
DHSID                                                  ...   
AL200800000001                               0.703046  ...   
AL200800000002                               0.636434  

In [22]:
labels = dd.read_csv(label_filename, usecols = pred_cols + ['DHSID'], dtype = {'Stunted_Rate':'float64'}).set_index('DHSID')
labels.head()

Mean_BMI  Median_BMI  Unmet_Need_Rate  Under5_Mortality_Rate  \
DHSID                                                                          
AL200800000001     24.12       25.28            50.00                   9.68   
AL200800000002     23.04       21.98             7.69                   8.33   
AL200800000004     26.74       26.57             7.69                   2.86   
AL200800000006     27.58       28.08             0.00                   9.52   
AL200800000010     24.23       23.77            20.00                  23.81   

                Skilled_Birth_Attendant_Rate  Stunted_Rate  
DHSID                                                       
AL200800000001                        100.00          20.0  
AL200800000002                         66.67           0.0  
AL200800000004                        100.00           0.0  
AL200800000006                           NaN           0.0  
AL200800000010                         50.00           0.0

In [23]:
labels.isnull().sum().compute()

Mean_BMI                        18517
Median_BMI                      18517
Unmet_Need_Rate                  1867
Under5_Mortality_Rate           29623
Skilled_Birth_Attendant_Rate    33279
Stunted_Rate                    58047
dtype: int64

In [5]:
train = labels.join(df, how='outer')
train.to_parquet('../Data/train/')

/opt/miniconda3/envs/ml2/lib/python3.10/site-packages/distributed/worker.py:3031: UserWarning: Large object of size 1.01 MiB detected in task graph: 
  {'how': 'outer', 'suffixes': ('', ''), 'indicator' ... 11926 columns]}
Consider scattering large objects ahead of time
with client.scatter to reduce scheduler burden and 
keep data on workers

    future = client.submit(func, big_data)    # bad

    big_future = client.scatter(big_data)     # good
    future = client.submit(func, big_future)  # good
  warnings.warn(
2023-06-12 10:08:52,315 - distributed.worker.memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. -- Unmanaged memory: 1.58 GiB -- Worker memory limit: 2.00 GiB
2023-06-12 10:09:27,621 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 1

In [6]:
sub = dd.read_csv('../Data/sample submission.csv', dtype={'DHSID': 'str'}).set_index('DHSID')
sub.head()

Mean_BMI  Median_BMI  Unmet_Need_Rate  Under5_Mortality_Rate  \
DHSID                                                                          
AL200800000003        20          20               50                     50   
AL200800000005        20          20               50                     50   
AL200800000007        20          20               50                     50   
AL200800000008        20          20               50                     50   
AL200800000009        20          20               50                     50   

                Skilled_Birth_Attendant_Rate  Stunted_Rate  
DHSID                                                       
AL200800000003                            50            50  
AL200800000005                            50            50  
AL200800000007                            50            50  
AL200800000008                            50            50  
AL200800000009                            50            50

In [7]:
test = sub.join(df, how='left')
test = test.drop(pred_cols, axis=1)

In [8]:
test = test.to_parquet('../Data/test/')

2023-06-12 10:39:55,537 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
2023-06-12 10:40:04,783 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
2023-06-12 10:40:04,787 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
2023-06-12 10:40:04,789 - distributed.utils_perf - WARNING - full garbage collections took 23% CPU time recently (threshold: 10%)
2023-06-12 10:40:05,044 - distributed.utils_perf - WARNING - full garbage collections took 32% CPU time recently (threshold: 10%)
2023-06-12 10:40:05,061 - distributed.utils_perf - WARNING - full garbage collections took 27% CPU time recently (threshold: 10%)
2023-06-12 10:40:05,067 - distributed.utils_perf - WARNING - full garbage collections took 25% CPU time recently (threshold: 10%)
2023-06-12 10:40:05,070 - distributed.utils_perf - WARNING - full garbage collections took

In [16]:
temp = temp.compute()
temp.isnull().sum()

ADM1DHS            0
ADM1FIPS       76609
ADM1FIPSNA     76609
ADM1NAME       15342
ADM1SALBCO     95106
ADM1SALBNA     95106
ADM1SALNA     120984
dtype: int64

In [18]:
temp['ADM1DHS']

0      9999
1      9999
2      9999
3      9999
4      9999
       ... 
883       9
884       1
885       4
886       9
887       3
Name: ADM1DHS, Length: 120984, dtype: object

In [7]:
temp1 = dd.read_csv(input_filename, sample=1000000, usecols=['ALT_DEM', 'ALT_GPS', 'CCFIPS','DATUM'])
temp1 = temp1.compute()
temp1

/opt/miniconda3/envs/ml2/lib/python3.10/site-packages/dask/dataframe/io/csv.py:193: DtypeWarning: Columns (11) have mixed types. Specify dtype option on import or set low_memory=False.
  df = reader(bio, **kwargs)


ALT_DEM  ALT_GPS CCFIPS  DATUM
0       45.0     39.0     AL  WGS84
1       65.0     92.0     AL  WGS84
2      261.0     41.0     AL  WGS84
3       29.0     22.0     AL  WGS84
4      130.0     47.0     AL  WGS84
..       ...      ...    ...    ...
883   1482.0   9999.0     ZW  WGS84
884   1448.0   9999.0     ZW  WGS84
885   1182.0   9999.0     ZW  WGS84
886   1416.0   9999.0     ZW  WGS84
887   1413.0   9999.0     ZW  WGS84

[120984 rows x 4 columns]

In [8]:
temp1.isnull().sum()

ALT_DEM       0
ALT_GPS       0
CCFIPS     1258
DATUM         0
dtype: int64

In [12]:
temp1['ALT_DEM'].unique().shape

(4352,)

In [14]:
temp2 = dd.read_csv(input_filename, sample=1000000, usecols=['ZONECO', 'ZONENA', 'DHSCLUST', 'DHSREGCO', 'SOURCE'], dtype=str)
temp2 = temp2.compute()
temp2

DHSCLUST DHSREGCO SOURCE ZONECO ZONENA
0          1        2    GPS    NaN    NaN
1          2        2    GPS    NaN    NaN
2          3        2    GPS    NaN    NaN
3          4        2    GPS    NaN    NaN
4          5        2    GPS    NaN    NaN
..       ...      ...    ...    ...    ...
883      396        9    GPS    NaN    NaN
884      397        1    GPS    NaN    NaN
885      398        4    GPS    NaN    NaN
886      399        9    GPS    NaN    NaN
887      400        3    GPS    NaN    NaN

[120984 rows x 5 columns]

In [17]:
temp2['DHSCLUST'].unique()

array(['1', '2', '3', ..., '6302', '7303', '7304'], dtype=object)

In [4]:
null_cols

Index(['BurnDate_kurtosis@MODIS/006/MCD64A1&timestamped',
       'Cloud_kurtosis@MODIS/006/MOD44B&timestamped',
       'Cloud_skew@MODIS/006/MOD44B&timestamped',
       'Dormancy_1_kurtosis@MODIS/006/MCD12Q2&timestamped',
       'Dormancy_1_skew@MODIS/006/MCD12Q2&timestamped',
       'Dormancy_2_kurtosis@MODIS/006/MCD12Q2&timestamped',
       'Dormancy_2_skew@MODIS/006/MCD12Q2&timestamped',
       'ESP@LANDFIRE/Vegetation/ESP/v1_2_0/AK',
       'ESP@LANDFIRE/Vegetation/ESP/v1_2_0/CONUS',
       'ESP@LANDFIRE/Vegetation/ESP/v1_2_0/HI',
       ...
       'z_min_max@GRIDMET/DROUGHT&timestamped',
       'z_min_min@GRIDMET/DROUGHT&timestamped',
       'z_skew@GRIDMET/DROUGHT&timestamped',
       'z_smoothed@CPOM/CryoSat2/ANTARCTICA_DEM',
       'z_smoothed_max@CPOM/CryoSat2/ANTARCTICA_DEM',
       'z_smoothed_min@CPOM/CryoSat2/ANTARCTICA_DEM',
       'z_stdDev@GRIDMET/DROUGHT&timestamped',
       'z_uncertainty@CPOM/CryoSat2/ANTARCTICA_DEM',
       'z_uncertainty_max@CPOM/CryoSat2/ANTARCTIC

In [5]:
# # get list of columns with over 50% null values
# null_cols = df.columns[df.isnull().mean() > 0.5]
# null_cols

In [6]:
# drop columns with over 50% null values
df = df[df.columns.difference(null_cols)]
df.head()

1@NASA/JPL/global_forest_canopy_height_2005  \
0                                     5.311582   
1                                     9.459806   
2                                    13.515421   
3                                     7.444454   
4                                     7.780849   

   1_max@NASA/JPL/global_forest_canopy_height_2005  \
0                                               14   
1                                               17   
2                                               15   
3                                               13   
4                                               15   

   1_min@NASA/JPL/global_forest_canopy_height_2005  \
0                                                0   
1                                                0   
2                                               12   
3                                                0   
4                                                0   

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_kurtosis@MODIS/061/MOD08_M3&timestamped  \
0                                               -3.0                                          
1                                               -3.0                                          
2                                               -3.0                                          
3                                               -3.0                                          
4                                               -3.0                                          

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_max@MODIS/061/MOD08_M3&timestamped  \
0                                                361                                         
1                                                361                                         
2                                                361                                         
3                                                361                                         
4                                                361                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_min@MODIS/061/MOD08_M3&timestamped  \
0                                                361                                         
1                                                300                                         
2                                                361                                         
3                                                361                                         
4                                                361                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_mean@MODIS/061/MOD08_M3&timestamped  \
0                                          220.33333                                      
1                                          179.06818                                      
2                                          220.33333                                      
3                                          220.33333                                      
4                                          220.33333                                      

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_median@MODIS/061/MOD08_M3&timestamped  \
0                                              246.5                                        
1                                              191.5                                        
2                                              246.5                                        
3                                              246.5                                        
4                                              246.5                                        

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_min_max@MODIS/061/MOD08_M3&timestamped  \
0                                                 78                                         
1                                                 78     

In [7]:
# with open('../Data/null_cols.pkl', 'wb') as f:
#     pickle.dump(null_cols, f)

In [8]:
# # find low variance columns
# # numerical_cols = df.select_dtypes(include=np.number).columns
# low_variance_cols = df.columns[df.var() < 0.01]
# len(low_variance_cols)

In [6]:
len(low_variance_cols)

70

In [9]:
# low_variance_cols

In [10]:
# drop low variance columns
df = df[df.columns.difference(low_variance_cols)]

In [11]:
df.head()

1@NASA/JPL/global_forest_canopy_height_2005  \
0                                     5.311582   
1                                     9.459806   
2                                    13.515421   
3                                     7.444454   
4                                     7.780849   

   1_max@NASA/JPL/global_forest_canopy_height_2005  \
0                                               14   
1                                               17   
2                                               15   
3                                               13   
4                                               15   

   1_min@NASA/JPL/global_forest_canopy_height_2005  \
0                                                0   
1                                                0   
2                                               12   
3                                                0   
4                                                0   

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_kurtosis@MODIS/061/MOD08_M3&timestamped  \
0                                               -3.0                                          
1                                               -3.0                                          
2                                               -3.0                                          
3                                               -3.0                                          
4                                               -3.0                                          

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_max@MODIS/061/MOD08_M3&timestamped  \
0                                                361                                         
1                                                361                                         
2                                                361                                         
3                                                361                                         
4                                                361                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_min@MODIS/061/MOD08_M3&timestamped  \
0                                                361                                         
1                                                300                                         
2                                                361                                         
3                                                361                                         
4                                                361                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_mean@MODIS/061/MOD08_M3&timestamped  \
0                                          220.33333                                      
1                                          179.06818                                      
2                                          220.33333                                      
3                                          220.33333                                      
4                                          220.33333                                      

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_median@MODIS/061/MOD08_M3&timestamped  \
0                                              246.5                                        
1                                              191.5                                        
2                                              246.5                                        
3                                              246.5                                        
4                                              246.5                                        

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_min_max@MODIS/061/MOD08_M3&timestamped  \
0                                                 78                                         
1                                                 78     

In [12]:
# with open('../Data/low_variance_cols.pkl', 'wb') as f:
#     pickle.dump(low_variance_cols, f)

In [13]:
imputer = si()
df = imputer.fit_transform(df)

2023-05-31 21:32:01,052 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:32:01,291 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:32:01,467 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:32:21,315 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:33:06,495 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:33:06,717 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:33:06,921 - distributed.utils_perf - WARNING - full garbage collections took 10% CPU time recently (threshold: 10%)
2023-05-31 21:33:07,202 - distributed.utils_perf - WARNING - full garbage collections took

In [14]:
scaler = ss()
df = scaler.fit_transform(df)

In [15]:
df.head()

1@NASA/JPL/global_forest_canopy_height_2005  \
0                                    -0.003928   
1                                     0.564414   
2                                     1.120067   
3                                     0.288293   
4                                     0.334382   

   1_max@NASA/JPL/global_forest_canopy_height_2005  \
0                                        -0.063792   
1                                         0.013014   
2                                        -0.038190   
3                                        -0.089394   
4                                        -0.038190   

   1_min@NASA/JPL/global_forest_canopy_height_2005  \
0                                        -0.209007   
1                                        -0.209007   
2                                         0.094017   
3                                        -0.209007   
4                                        -0.209007   

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_kurtosis@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.254546                                          
1                                          -0.254546                                          
2                                          -0.254546                                          
3                                          -0.254546                                          
4                                          -0.254546                                          

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_max@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.580573                                         
1                                          -0.580573                                         
2                                          -0.580573                                         
3                                          -0.580573                                         
4                                          -0.580573                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_max_min@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.573026                                         
1                                          -0.708704                                         
2                                          -0.573026                                         
3                                          -0.573026                                         
4                                          -0.573026                                         

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_mean@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.511735                                      
1                                          -0.725349                                      
2                                          -0.511735                                      
3                                          -0.511735                                      
4                                          -0.511735                                      

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_median@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.315941                                        
1                                          -0.661563                                        
2                                          -0.315941                                        
3                                          -0.315941                                        
4                                          -0.315941                                        

   AOD_550_Dark_Target_Deep_Blue_Combined_Mean_Mean_min_max@MODIS/061/MOD08_M3&timestamped  \
0                                          -0.699332                                         
1                                          -0.699332     

In [16]:
df.to_parquet('../Data/converted_data/')

2023-05-31 23:53:04,076 - distributed.worker.memory - WARNING - Unmanaged memory use is high. This may indicate a memory leak or the memory may not be released to the OS; see https://distributed.dask.org/en/latest/worker-memory.html#memory-not-released-back-to-the-os for more information. -- Unmanaged memory: 1.40 GiB -- Worker memory limit: 2.00 GiB


In [21]:
df = df.to_dask_array(lengths=True)

KeyboardInterrupt: 

In [ ]:
import gc
gc.collect()

537

In [ ]:
df.compute_chunk_sizes()

In [ ]:
pca = IncrementalPCA()
pca.fit(df)

TypeError: This estimator does not support dask dataframes. This might be resolved with one of

    1. ddf.to_dask_array(lengths=True)
    2. ddf.to_dask_array()  # may cause other issues because of unknown chunk sizes